# NDIS Project - OpenAI - PBSP Scoring - Page 4 - Reinforcement strategies to support teaching 

In [ ]:
import openai
import re
from ipywidgets import interact
import ipywidgets as widgets
from IPython.display import display, clear_output, Javascript, HTML, Markdown
import matplotlib.pyplot as plt
import matplotlib.ticker as mtick
import json
import spacy
from spacy import displacy
from dotenv import load_dotenv
import pandas as pd
import argilla as rg
from argilla.metrics.text_classification import f1
import warnings
warnings.filterwarnings('ignore')
%matplotlib inline
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_colwidth', 10000)
pd.set_option('display.width', 10000)

In [ ]:
#initializations
openai.api_key = os.environ['API_KEY']
openai.api_base = os.environ['API_BASE']
openai.api_type = os.environ['API_TYPE']
openai.api_version = os.environ['API_VERSION']
deployment_name = os.environ['DEPLOYMENT_ID']

#argilla
rg.init(
    api_url=os.environ["ARGILLA_API_URL"],
    api_key=os.environ["ARGILLA_API_KEY"]
)

In [ ]:
#sentence extraction
def extract_sentences(paragraph):
    symbols = ['\\.', '!', '\\?', ';', ':', ',', '\\_', '\n', '\\-']
    pattern = '|'.join([f'{symbol}' for symbol in symbols])
    sentences = re.split(pattern, paragraph)
    sentences = [sentence.strip() for sentence in sentences if sentence.strip()]
    return sentences

In [ ]:
def filter_dataframe(result_df, paragraph):
    filtered_df = pd.DataFrame(columns=result_df.columns)
    last_end = 0
    for index, row in result_df.iterrows():
        phrase = row['Phrase'].lower()
        if phrase in paragraph.lower()[last_end:]:
            filtered_df = filtered_df.append(row)
            last_end = paragraph.lower().find(phrase, last_end) + len(phrase)
        else:
            phrase_words = []
            for word in phrase.split():
                if word in paragraph.lower()[last_end:]:
                    phrase_words.append(word)
            filtered_phrase = " ".join(phrase_words)
            if len(filtered_phrase) / len(phrase) >= 0.9:
                filtered_row = row.copy()
                filtered_row['Phrase'] = filtered_phrase
                filtered_df = filtered_df.append(filtered_row)
                last_end = paragraph.lower().find(filtered_phrase, last_end) + len(filtered_phrase)
    return filtered_df

In [ ]:
def process_response(response, query):
    sentences = []
    topics = []
    scores = []
    lines = response.strip().split("\n")
    topic = None
    for line in lines:
        if "Privileges:" in line:
            topic = "PRIVILEGES"
        elif "Breaks:" in line:
            topic = "BREAKS"
        elif "Verbal Praise:" in line:
            topic = "VERBAL PRAISE"
        elif "Social Interaction:" in line:
            topic = "SOCIAL INTERACTION"
        elif "Physical Rewards:" in line:
            topic = "PHYSICAL REWARDS"
        elif "Attention:" in line:
            topic = "ATTENTION"
        elif "None:" in line:
            topic = "NO STRATEGY"
        else:
            try:
                parts = line.split("(Confidence Score:")
                if len(parts) == 2:
                    phrase = parts[0].strip()
                    score = float(parts[1].strip().replace(")", ""))
                    sentences.append(phrase)
                    topics.append(topic)
                    scores.append(score)
            except:
                pass
    result_df = pd.DataFrame({'Phrase': sentences, 'Topic': topics, 'Score': scores})
    try:
        result_df['Phrase'] = result_df['Phrase'].str.replace('\d+\.', '', regex=True)
        result_df['Phrase'] = result_df['Phrase'].str.replace('^\s', '', regex=True)
        result_df['Phrase'] = result_df['Phrase'].str.strip('"')
        result_df = filter_dataframe(result_df, query)
    except:
        sentences = extract_sentences(query)
        topics = ['NO STRATEGY'] * len(sentences)
        scores = [0.9] * len(sentences)
        result_df = pd.DataFrame({'Phrase': sentences, 'Topic': topics, 'Score': scores})
    return result_df

In [ ]:
def get_prompt(query):
    prompt = f"""
    The paragraph below is written by a disability practitioner in a behaviour support plan to describe the reinforcement strategies that will be used as a reward for completing work or demonstrating desired behavior while teaching the person with disability a new skill, an alternative behaviour or a functionally equivalent replacement behaviour.

    Paragraph:
    {query}

    Requirement:
    - Identify the phrases from the paragraph above that represent each of the following reinforcement strategies: "Privileges", "Breaks", "Verbal Praise", "Social Interaction", "Physical Rewards", "Attention".

    Guidelines:
    - "privileges": refers to allowing access to preferred activities such as dancing, singing, or playing, or access to preferred locations such as parks or gardens, as a reward for completing work or demonstrating desired behavior.
    - "breaks": refers to allowing breaks between lessons as a reward for completing work or demonstrating desired behavior.
    - "verbal praise": refers to providing verbal praise as a reward for completing work or demonstrating desired behavior, such as "great job!" or "i'm proud of you!"
    - "social interaction": refers to providing social interaction with preferred individuals, such as meeting with peers, parents, relatives, friends, as a reward for completing work or demonstrating desired behavior.
    - "physical rewards": refers to providing physical and tangible presents and gifts as a reward for completing work or demonstrating desired behavior, such as a lollipops, chocolates etc. 
    - "attention": refers to providing a form of positive interaction or engagement with the student as a reward for completing work or demonstrating desired behavior, such as sitting next to the student, offering help or guidance, or simply engaging in conversation with the student.

    Specifications of a correct answer:
    - Provide your answer in numbered lists. 
    - All the phrases in your answer must be exact substrings in the original paragraph. without changing any characters.
    - All the upper case and lower case characters in the phrases in your answer must match the upper case and lower case characters in the original paragraph.
    - Start numbering the phrases under each reinforcement strategy from number 1. 
    - Start each list of phrases with these titles: "Privileges", "Breaks", "Verbal Praise", "Social Interaction", "Physical Rewards", "Attention".
    - For each phrase that belongs to any of the above reinforcement strategies, provide a confidence score that ranges between 0.50 and 1.00, where a score of 0.50 means you are very weakly confident that the phrase belongs to that specific reinforcement strategy, whereas a score of 1.00 means you are very strongly confident that the phrase belongs to that specific reinforcement strategy.
    - Never include any phrase in your answer that does not exist in the paragraph above.
    - If there are not any phrases that belong to one or more of the reinforcement strategies, then do not include these strategies in your answer. 
    - Include a final numbered list titled "None:", which include all the remaining phrases from the paragraph above that do not belong to any of the reinforcement strategies above. Provide a confidence score for each of these phrases as well.

    Example answer:

    Privileges:
    1. <your phrase goes here>. (Confidence Score: <your score goes here>)
    2. <your phrase goes here>. (Confidence Score: <your score goes here>)

    Breaks:
    1. <your phrase goes here>. (Confidence Score: <your score goes here>)
    2. <your phrase goes here>. (Confidence Score: <your score goes here>)

    Verbal Praise:
    1. <your phrase goes here>. (Confidence Score: <your score goes here>)
    2. <your phrase goes here>. (Confidence Score: <your score goes here>)

    Social Interaction:
    1. <your phrase goes here>. (Confidence Score: <your score goes here>)
    2. <your phrase goes here>. (Confidence Score: <your score goes here>)

    Physical Rewards:
    1. <your phrase goes here>. (Confidence Score: <your score goes here>)
    2. <your phrase goes here>. (Confidence Score: <your score goes here>)

    Attention:
    1. <your phrase goes here>. (Confidence Score: <your score goes here>)
    2. <your phrase goes here>. (Confidence Score: <your score goes here>)
    
    None:
    1. <your phrase goes here>. (Confidence Score: <your score goes here>)
    2. <your phrase goes here>. (Confidence Score: <your score goes here>)
    """
    return prompt

In [ ]:
def get_response_chatgpt(prompt):
    response=openai.ChatCompletion.create(   
        engine=deployment_name,   
        messages=[         
        {"role": "system", "content": "You are a helpful assistant."},                  
        {"role": "user", "content": prompt}     
        ],
        temperature=0
    )
    reply = response["choices"][0]["message"]["content"]
    return reply

In [ ]:
def convert_df(result_df):
    new_df = pd.DataFrame(columns=['text', 'prediction'])
    new_df['text'] = result_df['Phrase']
    new_df['prediction'] = result_df.apply(lambda row: [[row['Topic'], row['Score']]], axis=1)
    return new_df

In [ ]:
#query = """
#When developing a positive behavior support plan for Eddie, I will use a combination of reinforcement strategies to encourage him to complete work and demonstrate desired behaviors while learning new skills. First, I will offer Eddie privileges by allowing him to participate in his preferred activities such as painting or playing games on the computer after completing his work. I will also provide breaks between lessons as a reward for completing work, such as a 10-minute break to play with his favorite toy.
#In addition, I will give Eddie verbal praise as a reward for demonstrating desired behaviors, such as saying "Great job, Eddie!" or "You worked really hard today." I will also offer social interaction as a reward by allowing him to spend time with his peers or family members, such as having lunch with his best friend or calling his grandmother on the phone.
#I will also provide physical rewards as a token of my appreciation for Eddie's efforts, such as stickers or small toys. Finally, I will give him attention by engaging in positive interactions with him, such as sitting with him while he completes his work and offering help and guidance when he needs it.
#By using a range of reinforcement strategies that reflect Eddie's preferences and interests, I hope to motivate him to complete his work and demonstrate positive behaviors during the learning process. The goal is to create a positive and supportive learning environment that encourages Eddie's success and builds his confidence.
#"""
#prompt = get_prompt(query)
#response = get_response_chatgpt(prompt)
#result_df = process_response(response, query)
#result_df

In [ ]:
topic_color_dict = {
        'PRIVILEGES': '#FFCCCC',
        'BREAKS': '#CCFFFF',
        'VERBAL PRAISE': '#FF69B4',
        'SOCIAL INTERACTION': '#FFFF00',
        'PHYSICAL REWARDS': '#CCCCFF',
        'ATTENTION': '#FFCC99',
        'NONE': '#F08080'
    }

def color(df, color):
    return df.style.format({'Score': '{:,.2%}'.format}).bar(subset=['Score'], color=color)

def annotate_query(highlights, query, topics):
    ents = []
    for h, t in zip(highlights, topics):
        pattern = re.escape(h)
        pattern = re.sub(r'\\(.)', r'[\1\\W]*', pattern) # optional non-alphanumeric characters
        for match in re.finditer(pattern, query, re.IGNORECASE):
            ent_dict = {"start": match.start(), "end": match.end(), "label": t}
            ents.append(ent_dict)
    return ents

def path_to_image_html(path):
    return '<img src="'+ path + '" width="30" height="15" />'

passing_score = 0.7
final_passing = 0.0
def display_final_df(agg_df):
    tags = []
    crits = [
            'PRIVILEGES',
            'BREAKS',
            'VERBAL PRAISE',
            'SOCIAL INTERACTION',
            'PHYSICAL REWARDS',
            'ATTENTION'
        ]
    orig_crits = crits
    crits = [x for x in crits if x in agg_df.index.tolist()]
    bools = [agg_df.loc[crit, 'Final_Score'] > final_passing for crit in crits]
    paths = ['./thumbs_up.png' if x else './thumbs_down.png' for x in bools]
    df = pd.DataFrame({'Reinforcement Strategy': crits, 'USED': paths})
    rem_crits = [x for x in orig_crits if x not in crits]
    if len(rem_crits) > 0:
        df2 = pd.DataFrame({'Reinforcement Strategy': rem_crits, 'USED': ['./thumbs_down.png'] * len(rem_crits)})
        df = pd.concat([df, df2])
    df = df.set_index('Reinforcement Strategy')
    pd.set_option('display.max_colwidth', None)
    display(HTML('<div style="text-align: center;">' + df.to_html(classes=["align-center"], index=True, escape=False ,formatters=dict(USED=path_to_image_html)) + '</div>'))
    

### Teaching of a new skill, alternative behaviour or functionally equivalent replacement behaviour <font color='red'>(Reinforcement strategies to support teaching)</font>

In [ ]:
#demo with Voila

bhvr_label = widgets.Label(value='Please type your answer:')
bhvr_text_input = widgets.Textarea(
    value='',
    placeholder='Type your answer',
    description='',
    disabled=False,
    layout={'height': '300px', 'width': '90%'}
)

bhvr_nlp_btn = widgets.Button(
    description='Score Answer',
    disabled=False,
    button_style='success', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Score Answer',
    icon='check',
    layout={'height': '70px', 'width': '250px'}
)
bhvr_agr_btn = widgets.Button(
    description='Validate Data',
    disabled=False,
    button_style='success', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Validate Data',
    icon='check',
    layout={'height': '70px', 'width': '250px'}
)
bhvr_eval_btn = widgets.Button(
    description='Evaluate Model',
    disabled=False,
    button_style='success', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Evaluate Model',
    icon='check',
    layout={'height': '70px', 'width': '250px'}
)
btn_box = widgets.HBox([bhvr_nlp_btn, bhvr_agr_btn, bhvr_eval_btn], 
                       layout={'width': '100%', 'height': '160%'})
bhvr_outt = widgets.Output()
bhvr_outt.layout.height = '100%'
bhvr_outt.layout.width = '100%'
bhvr_box = widgets.VBox([bhvr_text_input, btn_box, bhvr_outt], 
                   layout={'width': '100%', 'height': '160%'})
dataset_rg_name = 'pbsp-page4-reinforcement-strategy-argilla-ds'
agrilla_df = None
annotated = False
def on_bhvr_button_next(b):
    global agrilla_df
    with bhvr_outt:
        clear_output()
        query = bhvr_text_input.value
        prompt = get_prompt(query)
        response = get_response_chatgpt(prompt)
        result_df = process_response(response, query)
        sub_result_df = result_df[(result_df['Score'] >= passing_score) & (result_df['Topic'] != 'NO STRATEGY')]
        sub_2_result_df = result_df[result_df['Topic'] == 'NO STRATEGY']
        highlights = []
        if len(sub_result_df) > 0:
            highlights = sub_result_df['Phrase'].tolist()
            highlight_topics = sub_result_df['Topic'].tolist()    
            ents = annotate_query(highlights, query, highlight_topics)
            colors = {}
            for ent, ht in zip(ents, highlight_topics):
                colors[ent['label']] = topic_color_dict[ht]

            ex = [{"text": query,
                   "ents": ents,
                   "title": None}]
            title = "Reinforcement Strategy Highlights"
            display(HTML(f'<center><h1>{title}</h1></center>'))
            html = displacy.render(ex, style="ent", manual=True, jupyter=True, options={'colors': colors})
            display(HTML(html))
            title = "Reinforcement Strategy Classifications"
            display(HTML(f'<center><h1>{title}</h1></center>'))
            for top in topic_color_dict.keys():
                top_result_df = sub_result_df[sub_result_df['Topic'] == top]
                if len(top_result_df) > 0:
                    top_result_df = top_result_df.sort_values(by='Score', ascending=False).reset_index(drop=True)
                    top_result_df = top_result_df.set_index('Phrase')
                    top_result_df = top_result_df[['Score']]
                    display(HTML(
                        f'<left><h2 style="text-decoration: underline; text-decoration-color:{topic_color_dict[top]};">{top}</h2></left>'))
                    display(color(top_result_df, topic_color_dict[top]))

            agg_df = sub_result_df.groupby('Topic')['Score'].sum()
            agg_df = agg_df.to_frame()
            agg_df.index.name = 'Topic'
            agg_df.columns = ['Total Score']
            agg_df = agg_df.assign(
                Final_Score=lambda x: x['Total Score'] / x['Total Score'].sum() * 100.00
            )
            agg_df = agg_df.sort_values(by='Final_Score', ascending=False)
            title = "Reinforcement Strategy Coverage"
            display(HTML(f'<center><h1>{title}</h1></center>'))
            agg_df['Topic'] = agg_df.index
            rem_topics= [x for x in list(topic_color_dict.keys()) if not x in agg_df.Topic.tolist()]
            if len(rem_topics) > 0:
                rem_agg_df = pd.DataFrame({'Topic': rem_topics, 'Final_Score': 0.0, 'Total Score': 0.0})
                agg_df = pd.concat([agg_df, rem_agg_df])
            labels = agg_df['Final_Score'].round(1).astype('str') + '%'
            ax = agg_df.plot.bar(x='Topic', y='Final_Score', rot=0, figsize=(20, 5), align='center')
            for container in ax.containers:
                ax.bar_label(container, labels=labels)
                ax.yaxis.set_major_formatter(mtick.PercentFormatter())
                ax.legend(["Final Score (%)"])
                ax.set_xlabel('')
            plt.show()
            title = "Final Scores"
            display(HTML(f'<left><h1>{title}</h1></left>'))
            display_final_df(agg_df)
            if len(sub_2_result_df) > 0:
                sub_result_df = pd.concat([sub_result_df, sub_2_result_df]).reset_index(drop=True)
            agrilla_df = sub_result_df.copy()
        else:
            print(query)
            
def on_agr_button_next(b):
    global agrilla_df, annotated
    with bhvr_outt:
        clear_output()
        if agrilla_df is not None:
            # convert the dataframe to the structure accepted by argilla
            converted_df = convert_df(agrilla_df)
            # convert pandas dataframe to DatasetForTextClassification
            dataset_rg = rg.DatasetForTextClassification.from_pandas(converted_df)
            # delete the old DatasetForTextClassification from the Argilla web app if exists
            rg.delete(dataset_rg_name, workspace="admin")
            # load the new DatasetForTextClassification into the Argilla web app
            rg.log(dataset_rg, name=dataset_rg_name, workspace="admin")
            # Make sure all classes are present for annotation
            rg_settings = rg.TextClassificationSettings(label_schema=list(topic_color_dict.keys()))
            rg.configure_dataset(name=dataset_rg_name, workspace="admin", settings=rg_settings)
            annotated = True
        else:
            display(Markdown("<h2 style='color:red; text-align:center;'>Please score the answer first!</h2>"))
            
def on_eval_button_next(b):
    global annotated
    with bhvr_outt:
        clear_output()
        if annotated:
            display(f1(dataset_rg_name).visualize())
        else:
            display(Markdown("<h2 style='color:red; text-align:center;'>Please score the answer and validate the data first!</h2>"))

bhvr_nlp_btn.on_click(on_bhvr_button_next)
bhvr_agr_btn.on_click(on_agr_button_next)
bhvr_eval_btn.on_click(on_eval_button_next)

display(bhvr_label, bhvr_box)